## <center> Block 1. Data preparation </center>

In [1]:
# !conda install -c conda-forge shapely --yes 
# !conda install -c conda-forge pyproj --yes 
# !conda install -c conda-forge Beautifulsoup4 --yes 
# !conda install -c conda-forge lxml --yes 
# !conda install -c conda-forge html5lib --yes 
# !conda install -c conda-forge requests --yes 
# !conda install -c conda-forge geopy --yes
# !conda install -c conda-forge geocoder --yes

In [98]:
import requests
import pandas as pd
import numpy as np
import json
import geopy
import folium
from bs4 import BeautifulSoup
from geopy.geocoders import Nominatim
import shapely.geometry
import pyproj
import math
from shapely.geometry import shape, Point

In [108]:
pd.set_option('display.max_columns', 100)

I am going to create *work_with_tables()* function that can help me:
<br> 1. To find the number of rows and columns in the table </br>
<br> 2. To get cloumns titles </br>
<br> 3. To convert string to float </br>
<br> As a result of this function, i get the Pandas dataframe </br>

In [3]:
def work_with_tables(table):
    n_columns = 0
    n_rows=0
    column_names = []


    for row in table.find_all('tr'):
        
        td_tags = row.find_all('td')
        if len(td_tags) > 0:
            n_rows+=1
            if n_columns == 0:
                n_columns = len(td_tags)
                
        th_tags = row.find_all('th') 
        if len(th_tags) > 0 and len(column_names) == 0:
            for th in th_tags:
                column_names.append(th.get_text())

    if len(column_names) > 0 and len(column_names) != n_columns:
        raise Exception("Column titles do not match the number of columns")

    columns = column_names if len(column_names) > 0 else range(0,n_columns)
    df = pd.DataFrame(columns = columns,
                        index= range(0,n_rows))
    row_marker = 0
    for row in table.find_all('tr'):
        column_marker = 0
        columns = row.find_all('td')
        for column in columns:
            df.iat[row_marker,column_marker] = column.get_text()
            column_marker += 1
        if len(columns) > 0:
            row_marker += 1
            
    for col in df:
        try:
            df[col] = df[col].astype(float)
        except ValueError:
            pass
    
    return df

Then I load a page with Moscow Boroughs:

In [4]:
url = "https://gis-lab.info/qa/moscow-atd.html"
try:
    print('Try to request url "{}"'.format(url))
    response = requests.get(url)
    print('Url "{}" requested. '.format(url))
    
    soup = BeautifulSoup(response.text, 'lxml')
    tables = soup.findAll('table', { 'class' : 'wikitable sortable' }, limit=2) 
    Moscow_df = work_with_tables(tables[1])  
    print('Success'.format(url))

    Moscow_df.columns=["Borough_index", "Borough_Name", "District_Name", "Borough_Type", "OKATO_Code", "OKTMO_Code"]

    Moscow_df.to_csv("Moscow_df_raw.csv", index = False)

except Exception as err: 
    print('Request Url "{}" failed.'.format(url))
    print('Error is: {}'.format(err))
    Moscow_df = pd.read_csv("Moscow_df_raw.csv")

print(Moscow_df.head())
print(Moscow_df.shape)
print(Moscow_df.dtypes)

Try to request url "https://gis-lab.info/qa/moscow-atd.html"
Url "https://gis-lab.info/qa/moscow-atd.html" requested. 
Success
   Borough_index     Borough_Name District_Name           Borough_Type  \
0            1.0  Академический\n        ЮЗАО\n  Муниципальный округ\n   
1            2.0   Алексеевский\n        СВАО\n  Муниципальный округ\n   
2            3.0   Алтуфьевский\n        СВАО\n  Муниципальный округ\n   
3            4.0          Арбат\n         ЦАО\n  Муниципальный округ\n   
4            5.0       Аэропорт\n         САО\n  Муниципальный округ\n   

   OKATO_Code  OKTMO_Code  
0  45293554.0  45397000.0  
1  45280552.0  45349000.0  
2  45280554.0  45350000.0  
3  45286552.0  45374000.0  
4  45277553.0  45333000.0  
(146, 6)
Borough_index    float64
Borough_Name      object
District_Name     object
Borough_Type      object
OKATO_Code       float64
OKTMO_Code       float64
dtype: object


There are some problems with data types in the dataframe, so i should resolve this problem by converting data to int in some columns:

In [5]:
Moscow_df.drop("Borough_index", axis=1, inplace=True)
Moscow_df.replace('\n', '', regex=True, inplace=True)

Moscow_df["OKATO_Code"] = Moscow_df["OKATO_Code"].astype(int)
Moscow_df["OKTMO_Code"] = Moscow_df["OKTMO_Code"].astype(int)

print(Moscow_df.head())
print(Moscow_df.shape)

print(Moscow_df.dtypes)

Moscow_df.to_csv("Moscow_df.csv", index = False)

    Borough_Name District_Name         Borough_Type  OKATO_Code  OKTMO_Code
0  Академический          ЮЗАО  Муниципальный округ    45293554    45397000
1   Алексеевский          СВАО  Муниципальный округ    45280552    45349000
2   Алтуфьевский          СВАО  Муниципальный округ    45280554    45350000
3          Арбат           ЦАО  Муниципальный округ    45286552    45374000
4       Аэропорт           САО  Муниципальный округ    45277553    45333000
(146, 5)
Borough_Name     object
District_Name    object
Borough_Type     object
OKATO_Code        int32
OKTMO_Code        int32
dtype: object


Now i should get coordinates of boroughs:

In [6]:
from geopy.exc import GeocoderTimedOut

In [7]:
Moscow_coord_df = pd.DataFrame(columns=['Borough_Name', 'Latitude', 'Longitude'] )

geolocator = Nominatim(user_agent="foursquare_agent", timeout=10)


try:
    for Borough_Name, Borough_Type, District_Name in zip(Moscow_df['Borough_Name'], Moscow_df['Borough_Type'], Moscow_df['District_Name']):
        address = '{}, {}, {}, Москва, Россия'.format(Borough_Name, Borough_Type, District_Name)

        location = None

        for x in range(0, 9):
            try:
                location = geolocator.geocode(address)
                if location is not None:
                    latitude = location.latitude
                    longitude = location.longitude
                    Moscow_coord_df = Moscow_coord_df.append({'Borough_Name': Borough_Name, 'Latitude': latitude, 'Longitude': longitude}, ignore_index=True) 
                    break
            except Exception as err:
                print('')
                print(type(err))
                print(err) 
                raise


    Moscow_coord_df.to_csv("Moscow_coord_df.csv", index = False)

except Exception as err:
    print('')
    print(err)
    print('Request Nominatim failed')
    Moscow_coord_df = pd.read_csv("Moscow_coord_df.csv")


print(Moscow_coord_df.head())
print(Moscow_coord_df.shape)
print(Moscow_coord_df.dtypes)

    Borough_Name   Latitude  Longitude
0  Академический  55.689738  37.576771
1   Алексеевский  55.814222  37.639196
2   Алтуфьевский  55.902309  37.598674
3          Арбат  55.746223  37.589367
4       Аэропорт  55.800402  37.533156
(141, 3)
Borough_Name     object
Latitude        float64
Longitude       float64
dtype: object


Data loading from GIS-lab

In [8]:
url = 'http://gis-lab.info/data/mos-adm/mo.geojson'
try:
    print('Try to request url "{}"'.format(url))
    download_file = requests.get(url)
    print('Url "{}" requested. '.format(url))

    mo_geojson_utf8 = 'mo.geojson.utf8'
    open(mo_geojson_utf8, 'wb').write(download_file.content)    
    print('GeoJSON file downloaded!')

    mo_geojson = 'mo.geojson'

    f = open(mo_geojson, "wb")
    for line in open(mo_geojson_utf8, "rb"):
        f.write(line.decode('u8').encode('cp1251', 'ignore'))
    f = open(mo_geojson, "wb")
    for line in open(mo_geojson_utf8, "rb"):
        f.write(line.decode('u8').encode('cp1251', 'ignore'))

    with open(mo_geojson) as json_file:
        data = json_file.read()
        try:
            data = json.loads(data)
        except ValueError as e:
            print('invalid json: %s' % e)

except: 
    print('Request Url "{}" failed'.format(url))
    mo_geojson = 'mo.geojson'
    print('GeoJSON file downloaded!')

Try to request url "http://gis-lab.info/data/mos-adm/mo.geojson"
Url "http://gis-lab.info/data/mos-adm/mo.geojson" requested. 
GeoJSON file downloaded!


Work with Moscow Boroughs Housing Price dataset

In [9]:
url = "https://www.mirkvartir.ru/journal/analytics/2018/02/25/reiting-raionov-moskvi-po-stoimosti-kvartir"
try:
    print('Try to request url "{}"'.format(url))
    response = requests.get(url)
    print('Url "{}" requested. '.format(url))

    soup = BeautifulSoup(response.text, 'lxml')
    tables = soup.findAll('table', limit=1) 
    Moscow_housing_price_df = work_with_tables(tables[0])  

    Moscow_housing_price_df.to_csv("Moscow_housing_price_df_raw.csv", index = False)

except Exception as err: 
    print('Request Url "{}" failed'.format(url))
    print('Error is: {}'.format(err))
    Moscow_housing_price_df = pd.read_csv("Moscow_housing_price_df_raw.csv")


print(Moscow_housing_price_df.head())
print(Moscow_housing_price_df.shape)
print(Moscow_housing_price_df.dtypes)

Try to request url "https://www.mirkvartir.ru/journal/analytics/2018/02/25/reiting-raionov-moskvi-po-stoimosti-kvartir"
Url "https://www.mirkvartir.ru/journal/analytics/2018/02/25/reiting-raionov-moskvi-po-stoimosti-kvartir" requested. 
   0              1                 2               3                    4  \
0  №          Район  Цена, руб./кв. м  Прирост за год  Цена квартиры, руб.   
1  1          Арбат            438568          −0,20%             33702123   
2  2      Хамовники            425741           4,50%             27196303   
3  3       Якиманка            404471           1,30%             26920221   
4  4  Замоскворечье            398544           3,80%             26910141   

                5  
0  Прирост за год  
1           0,10%  
2           5,20%  
3           4,10%  
4           5,70%  
(144, 6)
0    object
1    object
2    object
3    object
4    object
5    object
dtype: object


Preparing Moscow Boroughs Housing Price dataset

In [10]:
Moscow_housing_price_df.drop([Moscow_housing_price_df.columns[0], Moscow_housing_price_df.columns[3], Moscow_housing_price_df.columns[4], Moscow_housing_price_df.columns[5]], axis=1, inplace=True)
Moscow_housing_price_df.drop(0, axis=0, inplace=True)

Moscow_housing_price_df.columns=["Borough_Name", "Borough_Housing_Price"]

Moscow_housing_price_df["Borough_Name"] = Moscow_housing_price_df["Borough_Name"].str.strip(' \n\t')

Moscow_housing_price_df.replace('\n', '', regex=True, inplace=True)

Moscow_housing_price_df["Borough_Housing_Price"] = Moscow_housing_price_df["Borough_Housing_Price"].astype(int)

# replace some Borough_Name as of russian letters "е" and "ё" and change places of some words 
Moscow_housing_price_df["Borough_Name"].replace('Бирюлево Восточное', 'Бирюлёво Восточное', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Бирюлево-Западное', 'Бирюлёво Западное', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Дегунино Восточное', 'Восточное Дегунино', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Измайлово Восточное', 'Восточное Измайлово', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Дегунино Западное', 'Западное Дегунино', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Савеловский', 'Савёловский', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Измайлово Северное', 'Северное Измайлово', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Медведково Северное', 'Северное Медведково', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Тушино Северное', 'Северное Тушино', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Теплый Стан', 'Тёплый Стан', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Тропарево-Никулино', 'Тропарёво-Никулино', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Филевский Парк', 'Филёвский Парк', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Хорошево-Мневники', 'Хорошёво-Мнёвники', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Хорошевский', 'Хорошёвский', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Черемушки', 'Черёмушки', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Медведково Южное', 'Южное Медведково', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Тушино Южное', 'Южное Тушино', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Мосрентген', '"Мосрентген"', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Бутово Северное', 'Северное Бутово', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Бутово Южное', 'Южное Бутово', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Десеновское', 'Десёновское', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Кленовское', 'Клёновское', regex=True, inplace=True)
Moscow_housing_price_df["Borough_Name"].replace('Новофедоровское', 'Новофёдоровское', regex=True, inplace=True)


print(Moscow_housing_price_df.head())
print(Moscow_housing_price_df.shape)
print(Moscow_housing_price_df.dtypes)

Moscow_housing_price_df.to_csv("Moscow_housing_price_df.csv", index = False)

    Borough_Name  Borough_Housing_Price
1          Арбат                 438568
2      Хамовники                 425741
3       Якиманка                 404471
4  Замоскворечье                 398544
5       Тверской                 386255
(143, 2)
Borough_Name             object
Borough_Housing_Price     int32
dtype: object


Work with Moscow Boroughs Population Density dataset 

In [11]:
url = "https://ru.wikipedia.org/wiki/%D0%A1%D0%BF%D0%B8%D1%81%D0%BE%D0%BA_%D1%80%D0%B0%D0%B9%D0%BE%D0%BD%D0%BE%D0%B2_%D0%B8_%D0%BF%D0%BE%D1%81%D0%B5%D0%BB%D0%B5%D0%BD%D0%B8%D0%B9_%D0%9C%D0%BE%D1%81%D0%BA%D0%B2%D1%8B"

try:
    print('Try to request url "{}"'.format(url))
    response = requests.get(url)
    print('Url "{}" requested. '.format(url))

    soup = BeautifulSoup(response.text, 'lxml')
    tables = soup.findAll('table', { 'class' : 'standard sortable' }, limit=1) 
    Moscow_dens_df = work_with_tables(tables[0]) 
    print('Success'.format(url))

    Moscow_dens_df.to_csv("Moscow_dens_df_raw.csv", index = False)

except Exception as err: 
    print('Request Url "{}" failed.'.format(url))
    print('Error is: {}'.format(err))
    Moscow_dens_df = pd.read_csv("Moscow_dens_df_raw.csv")


print(Moscow_dens_df.head(2))
print(Moscow_dens_df.shape)
print(Moscow_dens_df.dtypes)

Try to request url "https://ru.wikipedia.org/wiki/%D0%A1%D0%BF%D0%B8%D1%81%D0%BE%D0%BA_%D1%80%D0%B0%D0%B9%D0%BE%D0%BD%D0%BE%D0%B2_%D0%B8_%D0%BF%D0%BE%D1%81%D0%B5%D0%BB%D0%B5%D0%BD%D0%B8%D0%B9_%D0%9C%D0%BE%D1%81%D0%BA%D0%B2%D1%8B"
Url "https://ru.wikipedia.org/wiki/%D0%A1%D0%BF%D0%B8%D1%81%D0%BE%D0%BA_%D1%80%D0%B0%D0%B9%D0%BE%D0%BD%D0%BE%D0%B2_%D0%B8_%D0%BF%D0%BE%D1%81%D0%B5%D0%BB%D0%B5%D0%BD%D0%B8%D0%B9_%D0%9C%D0%BE%D1%81%D0%BA%D0%B2%D1%8B" requested. 
Success
     № Флаг Герб Название района[2]/поселения[3][4]  \
0  1.0                               Академический    
1  2.0                                Алексеевский    

  Название cоответствующего внутригородского муниципального образования: муниципального округа / поселения / городского округа[5]  \
0                                     Академический                                                                                 
1                                      Алексеевский                                                    

Preparing Moscow Boroughs Population Density dataset

In [12]:
Moscow_dens_df.drop([Moscow_dens_df.columns[0], Moscow_dens_df.columns[1], Moscow_dens_df.columns[2], Moscow_dens_df.columns[3], Moscow_dens_df.columns[5]], axis=1, inplace=True)

Moscow_dens_df.columns=["Borough_Name", "Borough_Area", "Borough_Population", "Borough_Population_Density", "Borough_Housing_Area", "Borough_Housing_Area_Per_Person"]

Moscow_dens_df["Borough_Name"].replace(', поселение ', '', regex=True, inplace=True)
Moscow_dens_df["Borough_Name"].replace(', городской округ ', '', regex=True, inplace=True)
Moscow_dens_df["Borough_Name"] = Moscow_dens_df["Borough_Name"].str.strip(' \n\t')
Moscow_dens_df["Borough_Name"].replace('Мосрентген', '"Мосрентген"', regex=True, inplace=True)

# Replace '\n' and ' ↗' in some columns
Moscow_dens_df.replace('\n', '', regex=True, inplace=True)
Moscow_dens_df.replace('↗', '', regex=True, inplace=True)
Moscow_dens_df.replace('↘', '', regex=True, inplace=True)

# Delete extra spaces in numeric columns
Moscow_dens_df["Borough_Area"].replace(' ', '', regex=True, inplace=True)
Moscow_dens_df["Borough_Population"].replace('\xa0', '', regex=True, inplace=True)
Moscow_dens_df["Borough_Population"].replace(' ', '', regex=True, inplace=True)
Moscow_dens_df["Borough_Population_Density"].replace(' ', '', regex=True, inplace=True)
Moscow_dens_df["Borough_Housing_Area"].replace(' ', '', regex=True, inplace=True)
Moscow_dens_df["Borough_Housing_Area_Per_Person"].replace(' ', '', regex=True, inplace=True)

# Replace ',' to '.' for float columns
Moscow_dens_df["Borough_Area"].replace(',', '.', regex=True, inplace=True)
Moscow_dens_df["Borough_Housing_Area"].replace(',', '.', regex=True, inplace=True)
Moscow_dens_df["Borough_Housing_Area_Per_Person"].replace(',', '.', regex=True, inplace=True)

# Convert from string to numeric
Moscow_dens_df["Borough_Population"] = Moscow_dens_df["Borough_Population"].astype(int)
Moscow_dens_df["Borough_Population_Density"] = Moscow_dens_df["Borough_Population_Density"].astype(int)
Moscow_dens_df["Borough_Area"] = Moscow_dens_df["Borough_Area"].astype(float)
Moscow_dens_df['Borough_Housing_Area'] = pd.to_numeric(Moscow_dens_df['Borough_Housing_Area'], errors='coerce')
Moscow_dens_df['Borough_Housing_Area_Per_Person'] = pd.to_numeric(Moscow_dens_df['Borough_Housing_Area_Per_Person'], errors='coerce')


print(Moscow_dens_df.head())
print(Moscow_dens_df.shape)
print(Moscow_dens_df.dtypes)

Moscow_dens_df.to_csv("Moscow_dens_df.csv", index = False)

    Borough_Name  Borough_Area  Borough_Population  \
0  Академический          5.83              110038   
1   Алексеевский          5.29               80634   
2   Алтуфьевский          3.25               57697   
3          Арбат          2.11               36308   
4       Аэропорт          4.58               79541   

   Borough_Population_Density  Borough_Housing_Area  \
0                       18874                2467.0   
1                       15242                1607.9   
2                       17752                 839.3   
3                       17207                 731.0   
4                       17367                1939.7   

   Borough_Housing_Area_Per_Person  
0                             22.7  
1                             20.5  
2                             15.5  
3                             26.0  
4                             25.9  
(146, 6)
Borough_Name                        object
Borough_Area                       float64
Borough_Population         

Creating a result Moscow Boroughs dataset

In [13]:
Moscow_Borough_df = pd.merge(left=Moscow_df, right=Moscow_dens_df, how='left', left_on='Borough_Name', right_on='Borough_Name')
Moscow_Borough_df = pd.merge(left=Moscow_Borough_df, right=Moscow_coord_df, how='left', left_on='Borough_Name', right_on='Borough_Name')
Moscow_Borough_df = pd.merge(left=Moscow_Borough_df, right=Moscow_housing_price_df, how='left', left_on='Borough_Name', right_on='Borough_Name')

Moscow_Borough_df[pd.isnull(Moscow_Borough_df['Borough_Housing_Price'])]
Moscow_Borough_df.dropna(subset=['Borough_Housing_Price'], inplace=True)

Moscow_Borough_df[pd.isnull(Moscow_Borough_df['Borough_Housing_Area'])]
Moscow_Borough_df.dropna(subset=['Borough_Housing_Area'], inplace=True)

Moscow_Borough_df.reset_index(drop=True, inplace=True)


print(Moscow_Borough_df.head())
print(Moscow_Borough_df.shape)
print(Moscow_Borough_df.dtypes)

Moscow_Borough_df.to_csv("Moscow_Borough_df.csv", index = False)

    Borough_Name District_Name         Borough_Type  OKATO_Code  OKTMO_Code  \
0  Академический          ЮЗАО  Муниципальный округ    45293554    45397000   
1   Алексеевский          СВАО  Муниципальный округ    45280552    45349000   
2   Алтуфьевский          СВАО  Муниципальный округ    45280554    45350000   
3          Арбат           ЦАО  Муниципальный округ    45286552    45374000   
4       Аэропорт           САО  Муниципальный округ    45277553    45333000   

   Borough_Area  Borough_Population  Borough_Population_Density  \
0          5.83              110038                       18874   
1          5.29               80634                       15242   
2          3.25               57697                       17752   
3          2.11               36308                       17207   
4          4.58               79541                       17367   

   Borough_Housing_Area  Borough_Housing_Area_Per_Person   Latitude  \
0                2467.0                            

Now result dataset includes all necessary info

Creating a map of Moscow Boroughs

In [14]:
Moscow_Borough_df = pd.read_csv("Moscow_Borough_df.csv")
mo_geojson = 'mo.geojson'

Moscow_lat= 55.7504461
Moscow_lng= 37.6174943

Moscow_map = folium.Map(location=[Moscow_lat, Moscow_lng], zoom_start=10)

Moscow_map.choropleth(
    geo_data=mo_geojson,
    data=Moscow_Borough_df,
    name='Population Density',
    columns=['Borough_Name', 'Borough_Population'],
    key_on='feature.properties.NAME',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Borough Population in Moscow City'
)


for Borough_Name, lat, lng, Borough_Population in zip(Moscow_Borough_df['Borough_Name'], Moscow_Borough_df['Latitude'], Moscow_Borough_df['Longitude'], Moscow_Borough_df['Borough_Population']):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5, 
        color='blue',
        fill=True,
        popup=folium.Popup('{}, Москва, Россия ({:})'.format(Borough_Name, Borough_Population), parse_html=True),
        fill_color='black',
        fill_opacity=0.6
    ).add_to(Moscow_map)

    folium.Circle([lat, lng], radius=1000, color='red', fill=False).add_to(Moscow_map)

Moscow_map

In [43]:
Moscow_Circle_lat= 55.7398697
Moscow_Circle_lng= 37.5365271
Circle_radius=28000
folium.Circle([Moscow_Circle_lat,Moscow_Circle_lng], radius=Circle_radius, color='yellow', fill=False).add_to(Moscow_map)

Moscow_map

In [16]:
def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)


x, y = lonlat_to_xy(Moscow_lat, Moscow_lng)
lo, la = xy_to_lonlat(x, y)

Define a function to create a hexagonal grid of cells

In [17]:
def create_hexagonal_grid (lat, lon, distance_limit, cell_radius):
    center_x, center_y = lonlat_to_xy(lon, lat) 

    k = math.sqrt(3) / 2 
    x_min = center_x - distance_limit
    x_step = cell_radius *2 
    y_min = center_y - distance_limit - (int((distance_limit/cell_radius+1)/k)*k*(cell_radius *2) - (distance_limit*2))/2
    y_step = cell_radius *2  * k 
    
    latitudes = []
    longitudes = []
    cells_id = []
    distances_from_center = []
    xs = []
    ys = []
    for i in range(0, int((distance_limit/cell_radius+1)/k)):
        y = y_min + i * y_step
        x_offset = cell_radius if i%2==0 else 0
        for j in range(0, int(distance_limit/cell_radius+1)):
            x = x_min + j * x_step + x_offset
            distance_from_center = calc_xy_distance(center_x, center_y, x, y)
            if (distance_from_center <= (distance_limit+1)):
                lon, lat = xy_to_lonlat(x, y)
                latitudes.append(lat)
                longitudes.append(lon)
                cells_id.append('{},{}'.format(lat, lon))
                distances_from_center.append(distance_from_center)
                xs.append(x)
                ys.append(y)

    return pd.DataFrame(list(zip(cells_id, latitudes, longitudes)), columns =['Cell_id', 'Cell_Latitude', 'Cell_Longitude']) 

In [18]:

distance_limit = 10000
cell_radius = 300
Moscow_Circle_lat= 55.7398697
Moscow_Circle_lng= 37.5365271    

Moscow_cells_df =  create_hexagonal_grid(Moscow_Circle_lat, Moscow_Circle_lng, distance_limit, cell_radius)
print(Moscow_cells_df.shape[0], 'candidate neighborhood centers generated.')

# Visualize circle center location and candidate neighborhood centers
Moscow_cell_map = folium.Map(location=[Moscow_Circle_lat, Moscow_Circle_lng], zoom_start=12)

# Generate choropleth map with Borough Population
Moscow_cell_map.choropleth(
    geo_data=mo_geojson,
    data=Moscow_Borough_df,
    name='Population Density',
    columns=['Borough_Name', 'Borough_Population'],
    key_on='feature.properties.NAME',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Borough Population in Moscow City'
)

# Add grid of area candidates
for lat, lng in zip(Moscow_cells_df['Cell_Latitude'], Moscow_cells_df['Cell_Longitude']):
    folium.Circle([lat, lng], radius=cell_radius, color='blue', fill=False).add_to(Moscow_cell_map)

Moscow_cell_map

1009 candidate neighborhood centers generated.


In [19]:
distance_limit = 28000
cell_radius = 300

Moscow_Circle_lat= 55.7398697
Moscow_Circle_lng= 37.5365271    

Moscow_cells_df =  create_hexagonal_grid(Moscow_Circle_lat, Moscow_Circle_lng, distance_limit, cell_radius)
Moscow_cells_df.index = Moscow_cells_df['Cell_id']
print(Moscow_cells_df.shape[0], 'candidate neighborhood centers generated.')

# Save dataframe
Moscow_cells_df.to_csv("Moscow_cells_df.csv", index = False)

7899 candidate neighborhood centers generated.


Working with Foursquare API 

In [33]:
def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Россия', '')
    address = address.replace(', Москва', '')
    return address

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def get_venues_near_location(lat, lon, client_id, client_secret, radius=300, limit=100):
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, radius, limit)
#     print(url)
    results = requests.get(url).json()['response']['groups'][0]['items']
    venues = [(item['venue']['id'],
               item['venue']['name'],
               get_categories(item['venue']['categories']),
               item['venue']['location']['lat'], 
               item['venue']['location']['lng'],
               format_address(item['venue']['location']),
               item['venue']['location']['distance']) for item in results]        
    return venues

In [35]:
Moscow_venues_df = pd.DataFrame()
# Moscow_venues_df = pd.read_csv('Moscow_venues_df_raw.csv')
Moscow_cells_explored_df = pd.DataFrame(columns=['Cell_id'])
# Moscow_cells_explored_df = pd.read_csv('Moscow_cells_explored_df.csv')

In [110]:
Moscow_venues_df = pd.read_csv('Moscow_venues_df_raw.csv')
Moscow_cells_explored_df = pd.read_csv('Moscow_cells_explored_df.csv')

In [34]:
client_id = 'BVPNORTXKXSJSUGVAMOHSLJQUCQ10FGC0FCKERDEXM4TYJ3D'
client_secret = 'V1BNVL2W1SDBPI2BJTXBXVEKNJPRYH1POJN0LMCD2ZXVQWLL'
version = '20180604'

limit = 100
explore_radius = cell_radius+50

In [114]:
Moscow_cells_for_explore_df = Moscow_cells_df[~Moscow_cells_df['Cell_id'].isin(Moscow_cells_explored_df['Cell_id'])].head(1000)


for index, lat, lng in zip(Moscow_cells_for_explore_df.index, Moscow_cells_for_explore_df['Cell_Latitude'], Moscow_cells_for_explore_df['Cell_Longitude']):
    print('Explore Cell {}'.format(index), end='')
    
    try:
        venues = get_venues_near_location(lat, lng, client_id, client_secret, radius=explore_radius, limit=limit)
        print(' - found {} veenues'.format(len(venues)))

        if (len(venues) > 0):
            Moscow_venues_df = Moscow_venues_df.append([(index, lat, lng, v[0], v[1], v[2], v[3], v[4], v[5], v[6], "") for v in venues], ignore_index=True)

        Moscow_cells_explored_df.loc[index] = index 
        
    except Exception as err:
        print(err)
        pass

Moscow_cells_explored_df.to_csv("Moscow_cells_explored_df.csv", index = False)
Moscow_venues_df.to_csv("Moscow_venues_df_raw.csv", index = False)

Explore Cell 55.540214358690555,37.4976787558004'formattedAddress'
Explore Cell 55.64033324283021,37.92238114316508 - found 2 veenues
Explore Cell 55.638599429227995,37.9311594885869 - found 0 veenues
Explore Cell 55.80077467929833,37.11771806299213 - found 4 veenues
Explore Cell 55.79909544943888,37.12658399908791 - found 3 veenues
Explore Cell 55.797415613347056,37.135448995422784 - found 0 veenues
Explore Cell 55.79573517116918,37.14431305179439 - found 1 veenues
Explore Cell 55.7940541230516,37.15317616800055 - found 0 veenues
Explore Cell 55.79237246914074,37.162038343839306 - found 1 veenues
Explore Cell 55.79069020958301,37.17089957910891 - found 0 veenues
Explore Cell 55.78900734452484,37.17975987360779 - found 0 veenues
Explore Cell 55.7873238741127,37.1886192271346 - found 0 veenues
Explore Cell 55.785639798493065,37.19747763948819 - found 0 veenues
Explore Cell 55.78395511781247,37.20633511046762 - found 1 veenues
Explore Cell 55.78226983221744,37.21519163987211 - found 0 ve

Explore Cell 55.71956459468097,37.591563161917406 - found 17 veenues
Explore Cell 55.71785288670073,37.600380622102186 - found 27 veenues
Explore Cell 55.71614058013304,37.609197131408976 - found 12 veenues
Explore Cell 55.71442767512561,37.6180126896461 - found 29 veenues
Explore Cell 55.7127141718261,37.62682729662206 - found 6 veenues
Explore Cell 55.711000070382276,37.635640952145586 - found 9 veenues
Explore Cell 55.70928537094188,37.64445365602559 - found 4 veenues
Explore Cell 55.70757007365269,37.65326540807121 - found 25 veenues
Explore Cell 55.705854178662506,37.66207620809175 - found 18 veenues
Explore Cell 55.70413768611912,37.67088605589673 - found 6 veenues
Explore Cell 55.702420596170434,37.67969495129589 - found 9 veenues
Explore Cell 55.70070290896427,37.68850289409914 - found 8 veenues
Explore Cell 55.698984624648496,37.69730988411661 - found 1 veenues
Explore Cell 55.69726574337108,37.706115921158634 - found 0 veenues
Explore Cell 55.695546265279916,37.71492100503573

Explore Cell 55.674849386813385,37.845136394582966 - found 0 veenues
Explore Cell 55.673120399908605,37.85392747374366 - found 1 veenues
Explore Cell 55.671390818563346,37.86271759630633 - found 9 veenues
Explore Cell 55.66966064292597,37.871506762085026 - found 8 veenues
Explore Cell 55.667929873144836,37.880294970893964 - found 4 veenues
Explore Cell 55.6661985093684,37.889082222547586 - found 0 veenues
Explore Cell 55.664466551745036,37.89786851686051 - found 2 veenues
Explore Cell 55.66273400042323,37.90665385364756 - found 16 veenues
Explore Cell 55.661000855551436,37.915438232723794 - found 13 veenues
Explore Cell 55.659267117278155,37.92422165390442 - found 8 veenues
Explore Cell 55.657532785751876,37.93300411700486 - found 7 veenues
Explore Cell 55.655797861121165,37.94178562184077 - found 2 veenues
Explore Cell 55.81807433752668,37.12804909502596 - found 1 veenues
Explore Cell 55.816394022934595,37.13691831378277 - found 0 veenues
Explore Cell 55.814713101812075,37.14578659144

Explore Cell 55.79459189981135,37.27686876274391 - found 0 veenues
Explore Cell 55.79290132367487,37.285723243121595 - found 1 veenues
Explore Cell 55.791210143355,37.29457677875072 - found 1 veenues
Explore Cell 55.78951835899867,37.303429369432166 - found 5 veenues
Explore Cell 55.78782597075289,37.312281014967034 - found 0 veenues
Explore Cell 55.78613297876469,37.32113171515664 - found 0 veenues
Explore Cell 55.78443938318108,37.329981469802455 - found 0 veenues
Explore Cell 55.78274518414916,37.33883027870622 - found 0 veenues
Explore Cell 55.781050381816,37.3476781416698 - found 0 veenues
Explore Cell 55.77935497632873,37.35652505849533 - found 1 veenues
Explore Cell 55.777658967834476,37.36537102898511 - found 0 veenues
Explore Cell 55.77596235648037,37.37421605294165 - found 1 veenues
Explore Cell 55.77426514241364,37.3830601301677 - found 0 veenues
Explore Cell 55.772567325781466,37.39190326046615 - found 0 veenues
Explore Cell 55.770868906731096,37.400745443640126 - found 4 v

Explore Cell 55.70760271265438,37.77654781267325 - found 2 veenues
Explore Cell 55.70587797585495,37.78535067998569 - found 5 veenues
Explore Cell 55.704152642995865,37.79415259103865 - found 5 veenues
Explore Cell 55.70242671422548,37.80295354564432 - found 0 veenues
Explore Cell 55.700700189692185,37.8117535436151 - found 9 veenues
Explore Cell 55.69897306954434,37.82055258476354 - found 4 veenues
Explore Cell 55.697245353930356,37.82935066890244 - found 3 veenues
Explore Cell 55.695517042998674,37.83814779584478 - found 1 veenues
Explore Cell 55.69378813689778,37.846943965403746 - found 4 veenues
Explore Cell 55.6920586357761,37.85573917739272 - found 9 veenues
Explore Cell 55.69032853978217,37.8645334316253 - found 19 veenues
Explore Cell 55.6885978490645,37.87332672791528 - found 7 veenues
Explore Cell 55.68686656377163,37.88211906607662 - found 13 veenues
Explore Cell 55.68513468405213,37.890910445923524 - found 8 veenues
Explore Cell 55.6834022100546,37.89970086727039 - found 14

Explore Cell 55.77968204232457,37.48011971538073'groups'
Explore Cell 55.777977137237,37.48895788380135'groups'
Explore Cell 55.77627163076712,37.497795101557266'groups'
Explore Cell 55.77456552306264,37.50663136845366'groups'
Explore Cell 55.77285881427128,37.515466684295916'groups'
Explore Cell 55.77115150454078,37.5243010488896'groups'
Explore Cell 55.76944359401894,37.5331344620405'groups'
Explore Cell 55.767735082853534,37.54196692355462'groups'
Explore Cell 55.76602597119241,37.55079843323813'groups'
Explore Cell 55.76431625918339,37.559628990897416'groups'
Explore Cell 55.76260594697433,37.568458596339106'groups'
Explore Cell 55.76089503471314,37.57728724936995'groups'
Explore Cell 55.759183522547715,37.58611494979699'groups'
Explore Cell 55.75747141062602,37.594941697427394'groups'
Explore Cell 55.75575869909598,37.60376749206859'groups'
Explore Cell 55.754045388105574,37.61259233352816'groups'
Explore Cell 55.75233147780283,37.62141622161394'groups'
Explore Cell 55.75061696833

In [137]:
# Moscow_venues_df = pd.read_csv("Moscow_venues_df_raw.csv")
# Moscow_venues_df.to_csv("Moscow_venues_df_raw_BACKUP.csv", index = False)

# words_df, numbers_df = (Moscow_venues_df[Moscow_venues_df.columns[11:]], 
#                         Moscow_venues_df[Moscow_venues_df.columns[:11]])
# words_df, numbers_df = (words_df.dropna(how='all'),
#                         numbers_df.dropna(how='all'))
# words_df = words_df.rename(columns={'Cell_id':'0',
#                  'Cell_Latitude':'1',
#                  'Cell_Longitude':'2',
#                  'Venue_Id':'3',
#                  'Venue_Name':'4',
#                  'Venue_All_Categories':'5',
#                  'Venue_Latitude':'6',
#                  'Venue_Longitude':'7', 
#                  'Venue_Location':'8', 
#                  'Venue_Distance':'9',
#                  'Borough_Name':'10'}) 
# fin_venues_df = pd.concat((numbers_df, words_df), axis=0, join='inner', ignore_index=False, keys=None,
#           levels=None, names=None, verify_integrity=False, copy=True)
# fin_venues_df['10'] = np.nan
# del words_df, numbers_df
# fin_venues_df

In [138]:
# Moscow_venues_df = pd.read_csv("Moscow_venues_df_raw.csv")
# Moscow_venues_df.to_csv("Moscow_venues_df_raw_BACKUP.csv", index = False)

# words_df, numbers_df = (Moscow_venues_df[Moscow_venues_df.columns[11:]], 
#                         Moscow_venues_df[Moscow_venues_df.columns[:11]])
# words_df, numbers_df = (words_df.dropna(how='all'),
#                         numbers_df.dropna(how='all'))
# words_df = words_df.rename(columns={'0.1':'0',
#                  '1.1':'1',
#                  '2.1':'2',
#                  '3.1':'3',
#                  '4.1':'4',
#                  '5.1':'5',
#                  '6.1':'6',
#                  '7.1':'7', 
#                  '8.1':'8', 
#                  '9.1':'9',
#                  '10.1':'10'}) 
# fin_venues_df = pd.concat((numbers_df, words_df), axis=0, join='inner', ignore_index=False, keys=None,
#           levels=None, names=None, verify_integrity=False, copy=True)
# fin_venues_df['10'] = np.nan
# del words_df, numbers_df
# fin_venues_df

In [135]:
# fin_venues_df.to_csv("Moscow_venues_df_raw.csv", index = False)

In [136]:
Moscow_venues_df = pd.read_csv("Moscow_venues_df_raw.csv")
Moscow_venues_df

0          1          2  \
0       55.67695842926316,37.18672468925941  55.676958  37.186725   
1       55.67695842926316,37.18672468925941  55.676958  37.186725   
2       55.67695842926316,37.18672468925941  55.676958  37.186725   
3       55.67695842926316,37.18672468925941  55.676958  37.186725   
4       55.64659468143242,37.34558577603909  55.646595  37.345586   
...                                     ...        ...        ...   
17629   55.56278225568258,37.57999265921078  55.562782  37.579993   
17630   55.56278225568258,37.57999265921078  55.562782  37.579993   
17631   55.56278225568258,37.57999265921078  55.562782  37.579993   
17632   55.56278225568258,37.57999265921078  55.562782  37.579993   
17633  55.557657299626165,37.60633897616585  55.557657  37.606339   

                              3                                4  \
0      5850fa8818dc531c1fb939ea                 Мегафон Экспресс   
1      4fc10ddae4b08acecb4c714b                       Ретро кафе   
2      51cc6b8c498eaabf4b5fba29               ООО "VL Computers"   
3      4f3f5416e4b02d0e6b676a1b                   Рынок за КПП-1   
4      4d31b8455017a093fdf3419b  Салон красоты Наталии Волошиной   
...                         ...                              ...   
17629  4e400abb7d8b0e96108a84b1                 Sun And Wellness   
17630  4daad38ea86e771ea72bd7b5                   Сказка Востока   
17631  4f2f9333e4b05a84da150f34    Клиника эстетической медицины   
17632  5107eb7a7e2745d3c7bf8bee                            Дикси   
17633  4fcf76ace4b0bdc2b72db0f2   Tula SBS (Shuttle Bus Station)   

                                                       5          6  \
0      [('Mobile Phone Shop', '4f04afc02fb6e1c99f3db0...  55.678210   
1                 [('Café', '4bf58dd8d48988d16d941735')]  55.678093   
2      [('Electronics Store', '4bf58dd8d48988d1229517...  55.679381   
3               [('Market', '50be8ee891d4fa8dcc7199a7')]  55.678750   
4      [('Salon / Barbershop', '4bf58dd8d48988d110951...  55.643984   
...                                                  ...        ...   
17629   [('Massage Studio', '52f2ab2ebcbc57f1066b8b3c')]  55.564502   
17630       [('Restaurant', '4bf58dd8d48988d1c4941735')]  55.564040   
17631  [('Health & Beauty Service', '54541900498ea6cc...  55.564832   
17632  [('Convenience Store', '4d954b0ea243a5684a65b4...  55.561647   
17633      [('Bus Station', '4bf58dd8d48988d1fe931735')]  55.558591   

               7                                   8      9  10  
0      37.187960                             Власиха  159.0 NaN  
1      37.187721                             Власиха  140.0 NaN  
2      37.189140                              Россия  309.0 NaN  
3      37.188707                              Россия  235.0 NaN  
4      37.343332            ул. Шолохова, 30, 119634  323.0 NaN  
...          ...                                 ...    ...  ..  
17629  37.578733                              Россия  207.0 NaN  
17630  37.584581     Коктебельская ул. 11 с3, 117216  321.0 NaN  
17631  37.579823                       ул. Грина, 18  228.0 NaN  
17632  37.583065                       ул. Грина, 1г  231.0 NaN  
17633  37.605258  м.Домодедовская (Ореховый Бульвар)  124.0 NaN  

[17634 rows x 11 columns]

Rename all columns

In [139]:
column_names = ['Cell_id', 'Cell_Latitude', 'Cell_Longitude', 'Venue_Id', 'Venue_Name', 
              'Venue_All_Categories','Venue_Latitude', 'Venue_Longitude', 'Venue_Location', 'Venue_Distance', 'Borough_Name'] 

Moscow_venues_df.columns=column_names

print(Moscow_venues_df.head())
print(Moscow_venues_df.shape)
print(Moscow_venues_df.dtypes)

                               Cell_id  Cell_Latitude  Cell_Longitude  \
0  55.67695842926316,37.18672468925941      55.676958       37.186725   
1  55.67695842926316,37.18672468925941      55.676958       37.186725   
2  55.67695842926316,37.18672468925941      55.676958       37.186725   
3  55.67695842926316,37.18672468925941      55.676958       37.186725   
4  55.64659468143242,37.34558577603909      55.646595       37.345586   

                   Venue_Id                       Venue_Name  \
0  5850fa8818dc531c1fb939ea                 Мегафон Экспресс   
1  4fc10ddae4b08acecb4c714b                       Ретро кафе   
2  51cc6b8c498eaabf4b5fba29               ООО "VL Computers"   
3  4f3f5416e4b02d0e6b676a1b                   Рынок за КПП-1   
4  4d31b8455017a093fdf3419b  Салон красоты Наталии Волошиной   

                                Venue_All_Categories  Venue_Latitude  \
0  [('Mobile Phone Shop', '4f04afc02fb6e1c99f3db0...       55.678210   
1             [('Café', '4bf58dd

Delete duplicate venues

In [140]:
print('Unique Venues {} of {}'.format(Moscow_venues_df['Venue_Id'].nunique(), Moscow_venues_df['Venue_Id'].shape[0]))

Moscow_venues_df.drop_duplicates(subset ="Venue_Id", keep = 'first', inplace = True) 
Moscow_venues_df.reset_index(inplace = True) 

print(Moscow_venues_df.shape)

Unique Venues 14490 of 17634
(14490, 12)


Take a look at Vanue name, Venue Category Name and Venue Category Id

In [141]:
Moscow_venues_df['Venue_Category_Name'] = Moscow_venues_df['Venue_All_Categories'].apply(lambda x: x.strip('[()]').split(', ')[0].strip("'"))
Moscow_venues_df['Venue_Category_Id'] = Moscow_venues_df['Venue_All_Categories'].apply(lambda x: x.strip('[()]').split(', ')[1].strip("'"))
print(Moscow_venues_df[['Venue_Name', 'Venue_Category_Name', 'Venue_Category_Id']].head())

                        Venue_Name Venue_Category_Name  \
0                 Мегафон Экспресс   Mobile Phone Shop   
1                       Ретро кафе                Café   
2               ООО "VL Computers"   Electronics Store   
3                   Рынок за КПП-1              Market   
4  Салон красоты Наталии Волошиной  Salon / Barbershop   

          Venue_Category_Id  
0  4f04afc02fb6e1c99f3db0bc  
1  4bf58dd8d48988d16d941735  
2  4bf58dd8d48988d122951735  
3  50be8ee891d4fa8dcc7199a7  
4  4bf58dd8d48988d110951735  


Loading a GeoJSON file with Boroughs to create geometry shape and correlate each venue to Moscow Boroughs where they were placed

In [142]:
with open(mo_geojson) as json_file:
    geojson_data = json.loads(json_file.read())

    
for feature in geojson_data['features']:
    polygon = shape(feature['geometry'])
    borough_name = feature['properties']['NAME']


    for index, name, lat, lng in zip(Moscow_venues_df.index, Moscow_venues_df['Venue_Name'], Moscow_venues_df['Venue_Latitude'], Moscow_venues_df['Venue_Longitude']):
        point = Point(lng, lat)
    
        if polygon.contains(point):
            Moscow_venues_df.loc[index, 'Borough_Name'] = borough_name

In [143]:
print(Moscow_venues_df[['Venue_Name', 'Venue_Category_Name', 'Borough_Name']].head(10))

                        Venue_Name Venue_Category_Name      Borough_Name
0                 Мегафон Экспресс   Mobile Phone Shop               NaN
1                       Ретро кафе                Café               NaN
2               ООО "VL Computers"   Electronics Store               NaN
3                   Рынок за КПП-1              Market               NaN
4  Салон красоты Наталии Волошиной  Salon / Barbershop  Ново-Переделкино
5             Спортзал у Дяди Жени  Athletics & Sports  Ново-Переделкино
6                        Del Gusto  Italian Restaurant  Ново-Переделкино
7   Остановка «Лукинская улица, 1»            Bus Stop  Ново-Переделкино
8                 "Сеньор Помидор"   Food & Drink Shop  Ново-Переделкино
9                          Копейка    Department Store  Ново-Переделкино


Removing the venues that located outside of the Moscow districts

In [144]:
print('{} Venue placed outside Moscow Boroughs'.format(Moscow_venues_df[~Moscow_venues_df['Borough_Name'].isin(Moscow_Borough_df['Borough_Name'])].shape[0]))
Moscow_venues_df.drop(Moscow_venues_df[~Moscow_venues_df['Borough_Name'].isin(Moscow_Borough_df['Borough_Name'])].index, inplace=True)
Moscow_venues_df.reset_index(inplace = True) 
Moscow_venues_df.to_csv("Moscow_venues_df.csv", index = False)

3796 Venue placed outside Moscow Boroughs


The first block of loading, processing, and preparing data for further analysis is completed.

As a result of this block we got the following data: 

* Dataset of Moscow Boroughs;
* Geo coordinates of the each borough;
* GeoJSON format of each borough;
* Venues dataset with geo coordinates and categories.